In [1]:
# necessary imports

from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
import undetected_chromedriver as uc
from time import sleep
import pickle
import pandas as pd
from datetime import date
from datetime import datetime

# rating xpath: //span[contains(@class, 'form rating')]
# link xpath: //tr[@class='player_tr_2']//a[contains(@href,'23/')]

In [41]:
# driver execution and rules for better performance

chromeOptions = uc.ChromeOptions()
chromeOptions.add_argument('--blink-settings=imagesEnabled=false')

driver = uc.Chrome(options=chromeOptions)


In [ ]:
# Pull player links and overall rating stats

player_links = []
player_stats = []
page_count = 1

# while loop limit should be page no + 1
# check maximum page number before changing while loop value

while page_count != 733:

    link = f"https://www.futbin.com/players?page={page_count}"
    driver.get(link)
    print(f"Entered page {page_count}")
    sleep(1.5)

    rawelem = driver.find_elements(By.XPATH, "//tr[contains(@class, 'player_tr')]")
    rawstat = driver.find_elements(By.XPATH, "//span[contains(@class, 'form rating')]") # find links & stats by xpath

    for elem in rawelem:
        urlattr = elem.get_attribute("data-url")
        full_link = "https://futbin.com" + urlattr
        player_links.append(full_link) # create url string
    print("URLs pulled")
 
    for stat in rawstat:
        stats = stat.text
        player_stats.append(stats)
    print("Stats pulled") # append stats

    page_count += 1
print(player_links)

playerdict = dict(zip(player_links,player_stats)) # create a dict like: {link:stat,link:stat...}

with open("player_links.pkl", "wb") as fhand:
    pickle.dump(playerdict,fhand)



In [42]:
maindata = [] #raw data, designed as [{playerleftdata},[playerstatdata],...,{playerleftdata},[playerstatdata]]
statdict = {}
failed_links = []

with open("data/player_links.pkl", "rb") as fhand:
    playerdict = pickle.load(fhand) # load link pkl

linklist = [i for i in playerdict]

# The value in linklist should be index of the previous member + 1

for link in linklist[18390:]:
    try:
        driver.get(link)
        sleep(.5)
        print(f"entered page index {linklist.index(link)}, {link}")
        stattext = []

        leftheads = driver.find_elements(By.XPATH, '//table[@class="table  table-info"]/tbody/tr/th')
        leftvals = driver.find_elements(By.XPATH,'//table[@class="table  table-info"]/tbody/tr/td') # pull the stats on the left side of the page

        stgdata = dict(zip([a.text for a in leftheads],[b.text for b in leftvals])) # ONLY the data on left, stats not included

        stgdata["playerlink"] = link
        stgdata["Position"] = driver.find_element(By.XPATH,'/html/body/div[9]/div[15]/div/div/div[3]/div/div[1]/div[1]/div[2]/div[2]').text
        print("pulled the left data + concatenated pos,link") # find position stat

        rawstat = driver.find_elements(By.XPATH, '//*[@id="card-2"]/div[1]/div/div[2]/div[1]/div/div')
        for elem in rawstat:
            stg = elem.text.split("\n")
            stattext.extend(stg) # pull stats on middle (pace, shooting...)
        print("pulled stats")
        maindata.append(stgdata)
        maindata.append(stattext)
        print(f"{linklist.index(link)} concatenated to maindata") # concatenate position and stat text to maindata
    except Exception as e:
        print(e)
        failed_links.append(link) # on unexpected stop, pull the link that the driver is on
        break
    
for i in range(len(maindata)):
    print(maindata[i])

output_path = "output/"
file_name = f"raw_data{datetime.now().strftime('%Y%m%d-%H%M')}.pkl" # create a file based on current date-time
full_path = output_path + file_name

with open(full_path, "wb") as fhand:
    pickle.dump(maindata,fhand)

entered page index 18390, https://futbin.com/23/player/47328/amine-salama
pulled the left data + concatenated pos,link
pulled stats
18390 concatenated to maindata
entered page index 18391, https://futbin.com/23/player/47330/junior-noguera
pulled the left data + concatenated pos,link
pulled stats
18391 concatenated to maindata
entered page index 18392, https://futbin.com/23/player/47333/silas-nwankwo
pulled the left data + concatenated pos,link
pulled stats
18392 concatenated to maindata
entered page index 18393, https://futbin.com/23/player/47361/vetle-skjaervik
pulled the left data + concatenated pos,link
pulled stats
18393 concatenated to maindata
entered page index 18394, https://futbin.com/23/player/47365/halvor-rdlen-opsahl
pulled the left data + concatenated pos,link
pulled stats
18394 concatenated to maindata
entered page index 18395, https://futbin.com/23/player/47414/sammy-braybrooke
pulled the left data + concatenated pos,link
pulled stats
18395 concatenated to maindata
enter

In [39]:
# check the linklist on every run

for i in linklist[18390:]:
    print(i)

https://futbin.com/23/player/47328/amine-salama
https://futbin.com/23/player/47330/junior-noguera
https://futbin.com/23/player/47333/silas-nwankwo
https://futbin.com/23/player/47361/vetle-skjaervik
https://futbin.com/23/player/47365/halvor-rdlen-opsahl
https://futbin.com/23/player/47414/sammy-braybrooke
https://futbin.com/23/player/47426/valentin-adamo
https://futbin.com/23/player/47450/maxim-dekker
https://futbin.com/23/player/47464/ulrich-donovan-ewolo
https://futbin.com/23/player/47465/rodrigo-santana-da-silva
https://futbin.com/23/player/47489/enrique-taborga
https://futbin.com/23/player/47491/roberto-carlos-ramirez
https://futbin.com/23/player/47501/mathias-bernatene
https://futbin.com/23/player/47517/santiago-toloza
https://futbin.com/23/player/47522/jeanuel-belocian
https://futbin.com/23/player/47523/lion-semic
https://futbin.com/23/player/47537/edoardo-pierozzi
https://futbin.com/23/player/47540/simone-davi
https://futbin.com/23/player/47622/barry-lauwers
https://futbin.com/23/

In [ ]:
# Will be useful on data engineering

def list_to_dict(lst):
    for x in range(0,len(lst),2):
        statdict[lst[x]] = lst[x+1]

In [40]:
# save failed_links in a pickle, just in case (change the number on every run)

with open("output/failed_links/failed_links_12.pkl","wb") as fhand:
    pickle.dump(failed_links,fhand)

In [43]:
# Check if the LAST LINK of the newly created pkl is equal to failed_links[0]

x = linklist[21943]
y = failed_links[0]

x is y

IndexError: list index out of range

In [37]:
# Check the last member of latest raw_data.pkl

with open("output/raw_data20230815-1711.pkl","rb") as xhand: # user should change the date on raw_data.pkl name on every run
    loader = pickle.load(xhand) 
print(loader[-2])

{'Name': 'Idrissa Thiam', 'Alt POS': 'RM, CAM, LW', 'AcceleRATE': 'Controlled (?)', 'Club': 'CD Lugo', 'Nation': 'Mauritania', 'League': 'LaLiga SmartBank (ESP 2)', 'Skills': '2', 'Weak Foot': '3', 'Intl. Rep': '1', 'Foot': 'Right', 'Height': '177cm | 5\'10"', 'Weight': '61', 'Revision': 'Normal', 'Att. WR': 'High', 'Def. WR': 'Low', 'Price Updated': '12 mins ago - 2023-08-15 14:55:45', 'Origin': 'N\\A', 'B.Type': 'Lean', 'Age': '22 years old', 'ID': '266851', 'Club ID': '110831', 'League ID': '54', 'playerlink': 'https://futbin.com/23/player/47300/idrissa-thiam', 'Position': 'LM'}


21944
